In [1]:
from pathlib import Path
import pandas as pd
import numpy as np
import torch
from torch.fft import fft
import matplotlib.pyplot as plt
import plotly.express as px
from plotly import subplots

## Creating a signal 
We need a sample rate and a sample number
We take two frequencies $f_1$ and $f_2$ and modulate them so as they last 0.5s

In [2]:
SAMPLE_RATE = 5000 
NUM_SAMPLES = 10000
T = np.arange(0, NUM_SAMPLES / SAMPLE_RATE, 1/SAMPLE_RATE)
f1, f2 = 100, 800

# creating the signal, adding the two frequencies components
X = np.sin(2*np.pi * f1 * T) * np.maximum(np.sin(2*np.pi * (T - .1)), 0) 
X += np.sin(2*np.pi * f2 * T) * np.maximum(np.sin(2*np.pi * (T - .4)), 0)

# plot
fig = px.line(x=T, y=X)
fig.update_layout(xaxis_title='Time (s)', yaxis_title='Signal X')

## Computing the Fast Fourier Transform (FFT)
First manually, then using Pytorch fft module  
The handmade method relies on this formula :  
$\mathrm{FFT}_k = \sum\limits_{n=0}^{N} X_n e^{-i2\pi kn/N}$, with $N$ the NUM_SAMPLES and $X_n$ the X signal n-th sample  
Both give the same result, which is symetrical.
$f_1$ and $f_2$ are visible (100Hz and 800Hz)

In [3]:
# frequencies array
F = np.linspace(0, SAMPLE_RATE-1, NUM_SAMPLES) 

# torch
FFT_torch = torch.fft.fft(torch.tensor(X))

# handmade
T_norm = np.linspace(0, (NUM_SAMPLES-1)/NUM_SAMPLES, NUM_SAMPLES)
FFT_handmade = np.zeros((NUM_SAMPLES))
for k in range(NUM_SAMPLES):
    Z = X * np.exp(-1j * 2*np.pi* k * T_norm)
    FFT_handmade[k] = Z.sum()

# compare 
df_FFT = pd.DataFrame(data={"Frequency": F, "FFT handmade": np.real(FFT_handmade), "FFT torch": np.real(FFT_torch)})
fig = px.line(df_FFT, x="Frequency", y=["FFT handmade", "FFT torch"])
fig.update_layout(xaxis_title='Frequency (Hz)', yaxis_title='FFT (real part)')

C:\Users\avenet\AppData\Local\Temp\ipykernel_13528\866956571.py:12: ComplexWarning:

Casting complex values to real discards the imaginary part



## Short Time Fourier Transfrom (STFT)
Computes several FFTs from different parts of the signal.  
Returns an image of frequencies in the signal given the time of the signal.  
We observe $f_1$ around $T=0.35s$ and $f_2$ around $T=0.65s$ 


In [4]:
N_FFT = 200
WIN_LENGTH = 200
HOP_LENGTH = 50
# usually win_length = n_fft 

# torch
STFT_torch = torch.stft(torch.tensor(X), n_fft=N_FFT, win_length=WIN_LENGTH,  hop_length=HOP_LENGTH, window=None, onesided=False, center=False)
STFT_torch.shape  # shape [N_FFT, (NUM_SAMPLES - WIN_LENGTH) / HOP_LENGTH + 1, 2]
STFT_torch = torch.stft(torch.tensor(X), n_fft=N_FFT, win_length=WIN_LENGTH,  hop_length=HOP_LENGTH, center=False)
STFT_torch.shape  # shape [N_FFT//2+1, (NUM_SAMPLES - WIN_LENGTH) / HOP_LENGTH + 1, 2]
# no more one sided, we are using the fft symetry property and we are not looking anymore to frequency > sample rate / 2

# handmade
N_W = N_FFT//2+1
N_M = (NUM_SAMPLES - WIN_LENGTH) // HOP_LENGTH + 1
T_norm = np.linspace(0, (WIN_LENGTH-1)/WIN_LENGTH, WIN_LENGTH)
# 
STFT_handmade = np.zeros((N_W, N_M))
for m in range(N_M):
    # print(m)
    Xm = X[m * HOP_LENGTH : m * HOP_LENGTH + WIN_LENGTH]
    FFTm = np.zeros((N_W))
    for w in np.arange(0, N_W): 
        Z = Xm * np.exp(-1j*2*np.pi*T_norm*w)
        FFTm[w] = np.real(Z.sum())
    #
    STFT_handmade[:, m] = FFTm

# Comparing real parts of each
STFT = np.dstack([STFT_handmade, STFT_torch[:, :, 0].numpy()]).transpose(2, 0, 1)
fig = px.imshow(STFT, animation_frame=0, x=np.arange(N_M) * NUM_SAMPLES / SAMPLE_RATE / N_M, y=np.arange(N_W) * (SAMPLE_RATE//2+1) / N_W, aspect="auto", labels=dict(x="Time (s)", y="Frequency (Hz)"))
fig.frames[0]['layout'].update(title_text=f'STFT handmade')
fig.frames[1]['layout'].update(title_text=f'STFT torch')
fig

c:\Users\avenet\Anaconda3\envs\torch\lib\site-packages\torch\functional.py:695: UserWarning:

stft will soon require the return_complex parameter be given for real inputs, and will further require that return_complex=True in a future PyTorch release. (Triggered internally at  C:\actions-runner\_work\pytorch\pytorch\builder\windows\pytorch\aten\src\ATen\native\SpectralOps.cpp:798.)



## Spectrogram
Pretty much the same as STFT, but we can add a weighted window (hann window here)  
Also we add complex part information now (taking module and not only real part)

In [5]:
# torch
from torchaudio.transforms import Spectrogram
transform = Spectrogram(n_fft=N_FFT, win_length=WIN_LENGTH, hop_length=HOP_LENGTH, center=False, power=2, onesided=True)
Spectrogram_torch = transform(torch.tensor(X, dtype=torch.float32))
Spectrogram_torch.shape  # [N_FFT, (len(X) - WIN_LENGTH) / HOP_LENGTH + 1]

# handmade
def hann_window(win_length):
    # return np.sin(np.pi * np.arange(win_length) / (win_length - 1))**2
    return np.sin(np.pi * np.arange(win_length) / (win_length))**2

window = hann_window(WIN_LENGTH)
N_W = N_FFT//2 + 1
N_M = (NUM_SAMPLES - WIN_LENGTH) // HOP_LENGTH + 1
T_norm = np.linspace(0, (WIN_LENGTH-1)/WIN_LENGTH, WIN_LENGTH)
# 
Spectrogram_handmade = np.zeros((N_W, N_M))
for m in range(N_M):
    # print(m)
    Xm = X[m * HOP_LENGTH : m * HOP_LENGTH + WIN_LENGTH]
    FFTm = np.zeros((N_W))
    for w in np.arange(0, N_W): 
        Z = Xm * np.exp(-1j*2*np.pi*T_norm*w)
        FFTm[w] = np.abs((Z * window).sum())**2
    #
    Spectrogram_handmade[:, m] = FFTm

# Comparing 
Spectrogram = np.dstack([Spectrogram_handmade, Spectrogram_torch.numpy()]).transpose(2, 0, 1)
fig = px.imshow(Spectrogram, animation_frame=0, x=np.arange(N_M) * NUM_SAMPLES / SAMPLE_RATE / N_M, y=np.arange(N_W) * (SAMPLE_RATE//2 + 1) / N_W, aspect="auto", labels=dict(x="Time (s)", y="Frequency (Hz)"))
fig.frames[0]['layout'].update(title_text=f'Spectrogram handmade')
fig.frames[1]['layout'].update(title_text=f'Spectrogram torch')
fig


## MelSpectrogram
Going from Hz to MelScale  
This is a logarithmic scale that better describes human perception of sounds

In [7]:
N_MELS = 64

# torch
# Apply MelScale to Spectrogram
from torchaudio.transforms import MelScale
transform = MelScale(n_mels=N_MELS, sample_rate=SAMPLE_RATE, n_stft=N_FFT//2+1, f_max=SAMPLE_RATE//2)
Spectrogram_torch.shape
MelSpectrogram_torch1 = transform(Spectrogram_torch)
MelSpectrogram_torch1.shape  # [N_MELS, (NUM_SAMPLES - WIN_LENGTH) // HOP_LENGTH + 1]

# Compute MelSpectrogram from signal directly
from torchaudio.transforms import MelSpectrogram
transform = MelSpectrogram(sample_rate=SAMPLE_RATE, n_fft=N_FFT, win_length=WIN_LENGTH, hop_length=HOP_LENGTH, center=False, onesided=True, n_mels=N_MELS)
MelSpectrogram_torch2 = transform(torch.tensor(X, dtype=torch.float32))
MelSpectrogram_torch2.shape

# handmade
import torchaudio
fb_torch = torchaudio.functional.melscale_fbanks(N_FFT//2+1, 0, SAMPLE_RATE//2, N_MELS, SAMPLE_RATE, None, "htk")
MelSpectrogram_torch3 = fb_torch.T @ Spectrogram_torch
# handmade fbanks
fb_handmade = np.zeros((N_FFT//2+1, N_MELS))
low_M, high_M = 0, 2595 * np.log10(1+SAMPLE_RATE/2/700)
M_bands = np.linspace(low_M, high_M, N_MELS)
F_bands = 700 * (10**(M_bands/2595) - 1)
F_bins = np.linspace(0, SAMPLE_RATE // 2, N_FFT//2+1)
for m in range(N_MELS):
    if m < N_MELS - 1:
        tr_sup = (F_bands[m+1] - F_bins) / (F_bands[m+1] - F_bands[m])
    else:
        tr_sup = np.zeros(N_FFT//2+1)
    if m > 0:
        tr_inf = (F_bins - F_bands[m-1]) / (F_bands[m] - F_bands[m-1])
    else:
        tr_inf = np.zeros(N_FFT//2+1)
    fb_handmade[:, m] = ((tr_sup > 0) & (tr_sup < 1)) * tr_sup + ((tr_inf > 0) & (tr_inf < 1)) * tr_inf

MelSpectrogram_handmade = fb_handmade.T @ Spectrogram_torch.numpy()


# Comparing 
MelSpectrograms = np.dstack([MelSpectrogram_torch1.numpy(), MelSpectrogram_torch2.numpy(), MelSpectrogram_torch3.numpy(), MelSpectrogram_handmade]).transpose(2, 0, 1)
fig = px.imshow(MelSpectrograms, animation_frame=0, x=np.arange(N_M) * NUM_SAMPLES / SAMPLE_RATE / N_M, y=M_bands, aspect="auto", labels=dict(x="Time (s)", y="Mel (Hz)"))
fig.frames[0]['layout'].update(title_text=f'MelSpectrogram from Spectrogram')
fig.frames[1]['layout'].update(title_text=f'MelSpectrogram from signal')
fig.frames[2]['layout'].update(title_text=f'MelSpectrogram from torch fbanks')
fig.frames[3]['layout'].update(title_text=f'MelSpectrogram handmade')
fig
